In [1]:
import os
from datetime import datetime, timedelta, timezone

import numpy as np
import pandas as pd
import matplotlib.pyplot as plt

import MetaTrader5 as mt5


Log in to mt5 using the icmarkets account credentials. You don't need the account credentials just to fetch the data.

In [ ]:
"""# ic- markets/ mt5 account  
LOGIN    = your_account_number              # int
PASSWORD = "password"                    # string
SERVER   = "ICMarketsSC-Demo"            # e.g., "MetaQuotes-Demo" or your broker's server name


# 2) login if credentials are provided (if terminal is already logged in, you can skip this)
if LOGIN and PASSWORD and SERVER:
    authorized = mt5.login(login=int(LOGIN), password=PASSWORD, server=SERVER)
    print("login:", authorized, mt5.last_error())"""

# initialize 
authorized = mt5.initialize()
print("initialize:", authorized, mt5.last_error())

# 3) quick check
info = mt5.account_info()
#info

initialize: True (1, 'Success')


In [3]:
SYM1 = "MS.NYSE"
SYM2 = "GS.NYSE"
TF = mt5.TIMEFRAME_H1 # try "H4" or "D1" later
START = datetime(2020, 1, 1) # UTC
END = datetime.now() # UTC

In [4]:
# get data
s1_rates = mt5.copy_rates_range(SYM1,TF,START, END)
s1_rates = pd.DataFrame(s1_rates)
s1_rates["time"] = pd.to_datetime(s1_rates["time"], unit = "s")
print(s1_rates)
s2_rates = mt5.copy_rates_range(SYM2,TF,START, END)
s2_rates = pd.DataFrame(s2_rates)
s2_rates["time"] = pd.to_datetime(s2_rates["time"], unit = "s")


                     time    open    high     low   close  tick_volume  \
0     2020-01-02 16:00:00   51.25   51.39   51.20   51.37          384   
1     2020-01-02 17:00:00   51.37   51.48   51.28   51.40          682   
2     2020-01-02 18:00:00   51.40   51.81   51.40   51.81          298   
3     2020-01-02 19:00:00   51.81   51.83   51.68   51.76          352   
4     2020-01-02 20:00:00   51.76   51.87   51.71   51.85          200   
...                   ...     ...     ...     ...     ...          ...   
10161 2025-10-17 18:00:00  158.42  159.95  157.83  159.76         1252   
10162 2025-10-17 19:00:00  159.74  160.20  158.99  159.14         1018   
10163 2025-10-17 20:00:00  159.15  159.15  158.15  158.90         1108   
10164 2025-10-17 21:00:00  158.91  159.82  158.91  159.54          981   
10165 2025-10-17 22:00:00  159.56  159.90  158.95  159.07         1238   

       spread  real_volume  
0           1            0  
1           1            0  
2           1           

In [5]:
df = s1_rates[["time", "open"]].merge(s2_rates[["time", "open"]], on = "time")

df = df.rename(columns={"open_x": SYM1, "open_y": SYM2})
print(df)

                     time  MS.NYSE  GS.NYSE
0     2020-01-02 16:00:00    51.25   230.66
1     2020-01-02 17:00:00    51.37   231.19
2     2020-01-02 18:00:00    51.40   231.68
3     2020-01-02 19:00:00    51.81   233.90
4     2020-01-02 20:00:00    51.76   234.12
...                   ...      ...      ...
10151 2025-10-15 22:00:00   163.20   766.32
10152 2025-10-16 16:00:00   163.91   777.28
10153 2025-10-16 17:00:00   162.46   766.05
10154 2025-10-16 18:00:00   163.30   776.52
10155 2025-10-16 19:00:00   163.04   775.66

[10156 rows x 3 columns]


In [6]:
# plot the df
import plotly.express as px
fig = px.line(df, x ="time", y = [SYM1, SYM2], title = f"Historical Prices - {SYM1} vs {SYM2}")

fig.show()

In [7]:
# investigate correlation using pandas method
df [[SYM1,SYM2]].corr()
# 99% correlation for xbr-xti

MS.NYSE   GS.NYSE
MS.NYSE  1.000000  0.964453
GS.NYSE  0.964453  1.000000

In [8]:
# compute the price differenc namely spread and use bb bands
df["price_difference"] = df[SYM1] - df[SYM2]

period = 200
df["sma"] = df ["price_difference"].rolling(period).mean()
df["standard_deviation"] = df["price_difference"].rolling(period).std()
df["lower_band"] = df["sma"] - 2 * df["standard_deviation"] 
df["upper_band"] = df["sma"] + 2 * df["standard_deviation"] 
df


time  MS.NYSE  GS.NYSE  price_difference        sma  \
0     2020-01-02 16:00:00    51.25   230.66           -179.41        NaN   
1     2020-01-02 17:00:00    51.37   231.19           -179.82        NaN   
2     2020-01-02 18:00:00    51.40   231.68           -180.28        NaN   
3     2020-01-02 19:00:00    51.81   233.90           -182.09        NaN   
4     2020-01-02 20:00:00    51.76   234.12           -182.36        NaN   
...                   ...      ...      ...               ...        ...   
10151 2025-10-15 22:00:00   163.20   766.32           -603.12 -628.01400   
10152 2025-10-16 16:00:00   163.91   777.28           -613.37 -628.14025   
10153 2025-10-16 17:00:00   162.46   766.05           -603.59 -628.20530   
10154 2025-10-16 18:00:00   163.30   776.52           -613.22 -628.32385   
10155 2025-10-16 19:00:00   163.04   775.66           -612.62 -628.42495   

       standard_deviation  lower_band  upper_band  
0                     NaN         NaN         NaN  
1                     NaN         NaN         NaN  
2                     NaN         NaN         NaN  
3                     NaN         NaN         NaN  
4                     NaN         NaN         NaN  
...                   ...         ...         ...  
10151           14.926349 -657.866698 -598.161302  
10152           14.692170 -657.524590 -598.755910  
10153           14.553179 -657.311658 -599.098942  
10154           14.331262 -656.986374 -599.661326  
10155           14.146696 -656.718342 -600.131558  

[10156 rows x 8 columns]

In [9]:
px.line(df, x= "time", y =["price_difference", "lower_band", "upper_band"], title=f" Price diffeence between {SYM1}-{SYM2} (mt5 price of timeframe {TF})")
                                                                                                                        


In [10]:
# pairs trading strategy signal generation
df["distance_from_mean"] = df["price_difference"] - df["sma"]
df["deviations_from_mean"] = df["distance_from_mean"] / df["standard_deviation"]

In [11]:
px.line(df, x= "time", y =["price_difference", "lower_band", "upper_band","sma", "distance_from_mean", "deviations_from_mean"], title=f" Price diffeence between {SYM1}-{SYM2} (mt5 price of timeframe {TF})")
